In [2]:
!pip install mapclassify
!pip install descartes 

In [3]:
import pandas as pd
import geopandas as gpd
import numpy as np
#import geoplot
from ipyleaflet import Map, GeoData, basemaps, LayersControl
from shapely.geometry import Point, Polygon
from geopandas.tools import overlay
import matplotlib.pyplot as plt
from matplotlib import cm
import mapclassify



In [4]:
%matplotlib qt
from matplotlib.animation import FuncAnimation
#plt.rcParams.update({'figure.max_open_warning': 0})

In [5]:
#adding a country zip file found online 
countries = gpd.read_file("zip://./world_countries.zip")
#turning the raw excel files into csv files and loading 
fall_2016 = pd.read_csv('Fall 2016 Migration.csv')
fall_2017 = pd.read_csv('Fall 2017 Migration.csv')
fall_2018 = pd.read_csv('Fall 2018 Migration.csv')
fall_2019 = pd.read_csv('Fall Migration 2019 .csv')

In [7]:
fall_2019 = fall_2019.sort_index(0,ascending = False)
fall_2016 = fall_2016.sort_index(0,ascending = False)


In [9]:
def month_avs(file):
    year_avs_lat  = np.array([])
    year_avs_lon  = np.array([])
    for m in range(8,12):
        month_av_lat = np.array([])
        month_av_lon = np.array([])
        for i in range(len(file.Date)):
            if file.Date[i][0:len(str(m))] == str(m):
                month_av_lat = np.append(month_av_lat, file.Lat[i])
                month_av_lon = np.append(month_av_lon, file.Lon[i])
            
        year_avs_lat = np.append(year_avs_lat,np.average(month_av_lat))   
        year_avs_lon = np.append(year_avs_lon,np.average(month_av_lon))
        
    #av_lat_lon = [(i,j) for i in year_avs_lat for j in year_avs_lon]
    av_lat_lon = list(zip(year_avs_lat,year_avs_lon))
    return av_lat_lon


In [10]:
av_2016 = month_avs(fall_2016)
av_2017 = month_avs(fall_2017)
av_2018 = month_avs(fall_2018)
av_2019 = month_avs(fall_2019)
print(av_2016)

[(44.075, -88.35), (40.69278846153846, -87.26394230769232), (34.3354066985646, -92.13157894736842), (27.29444444444444, -97.98333333333332)]


In [11]:
lat_2020 = np.array([])
lon_2020 = np.array([])
for i in range(len(av_2016)):
    lat_2020 = np.append(lat_2020, (av_2016[i][0]+av_2017[i][0]+av_2018[i][0]+av_2019[i][0])/4)
    lon_2020 = np.append(lon_2020, (av_2016[i][0]+av_2017[i][0]+av_2018[i][0]+av_2019[i][0])/4)
pred_2020 = list(zip(lat_2020,lon_2020))
pts_2020 = [Point(x[0], x[1]) for x in pred_2020] 
print(pts_2020)

[<shapely.geometry.point.Point object at 0x1197be400>, <shapely.geometry.point.Point object at 0x1197be470>, <shapely.geometry.point.Point object at 0x1197be518>, <shapely.geometry.point.Point object at 0x1197be550>]


In [12]:
#using the countries data frame to plot just North America 
north_america = countries[countries.continent == 'North America']
north_america = north_america[(north_america['iso_a3'] != 'GRL')]
NA = north_america[(north_america['name'] != 'Nunavut')]
NA.plot(color = 'green',figsize = (15,15))

In [13]:
#converting the latitude and longitude to point objects 
fall_2016['Point'] = [Point(fall_2016.Lon[i], fall_2016.Lat[i]) for i in range(fall_2016.shape[0])]
fall_2017['Point'] = [Point(fall_2017.Lon[i], fall_2017.Lat[i]) for i in range(fall_2017.shape[0])]
fall_2018['Point'] = [Point(fall_2018.Lon[i], fall_2018.Lat[i]) for i in range(fall_2018.shape[0])]
fall_2019['Point'] = [Point(fall_2019.Lon[i], fall_2019.Lat[i]) for i in range(fall_2019.shape[0])]

#converting the regular data frame into a geodataframe to overlay points 
pts_2016 = gpd.GeoDataFrame(fall_2016, geometry='Point')
pts_2017 = gpd.GeoDataFrame(fall_2017, geometry='Point')
pts_2018 = gpd.GeoDataFrame(fall_2018, geometry='Point')
pts_2019 = gpd.GeoDataFrame(fall_2019, geometry='Point')

In [14]:
ax = NA.plot(color='white', edgecolor='black',figsize = (15,15))
#plt.plot(pts_2016.Point[0], color = 'red')
pts_2017.plot(ax=ax, color='red')
plt.title('Fall 2016')
#pts_2018.plot(ax=ax, color='yellow')

Text(0.5, 1.0, 'Fall 2016')

In [39]:
pts_2016.iloc[1:2,[-1]]

Point
437  POINT (-100.40000 25.80000)

def display(A):
    #Display the graphics outside of the notebook. 
    #On a PC, use '%matplotlib qt' instead.
    %matplotlib qt
    
    plt.rcParams['figure.figsize'] = [15,15]
    plt.axis('off'); 
    plt.show()
    plt.draw()
    plt.pause(0.1)

In [1]:
nf = len(pts_2016)

for i in np.arange(1,nf,10):
    #plot background north america map
    #ax = fig.add_subplot(121,projection='2d')
    ax = NA.plot(color = 'white', edgecolor='black', figsize = (15,15))

    #plot each point 
    #fig = pts_2016.iloc[i:i+1,[-1]].plot(ax=ax, color='blue')
    pts_2016.head(i).plot(ax=ax, color='blue')  
    #plt.cla()
    plt.show()
    plt.draw()
    plt.pause(0.01)
       

NameError: name 'pts_2016' is not defined

In [ ]:
from matplotlib.animation import FFMpegWriter
metadata = dict(title='My first animation in 2D', artist='Matplotlib')
writer = FFMpegWriter(fps=15, metadata=metadata,bitrate=200000)
fig = plt.figure(dpi=200)

# fig = plt.figure() 
with writer.saving(fig, "2016.mp4", dpi=200):
    #fig, ax = plt.subplots()
    nf = len(pts_2016)
    for it in range(nf):
        for i in np.arange(1,len(pts_2016),10):
            #plot background north america map
            ax = NA.plot(color = 'white', edgecolor = 'black',figsize = (15,15))

            #plot each point 
            pts_2016.iloc[i:i+1,[-1]].plot(ax=ax, color='blue')
        
    
        plt.show()
        plt.draw()
        plt.pause(0.01)
        writer.grab_frame()
   
    
    

/anaconda3/lib/python3.7/site-packages/matplotlib/pyplot.py:514: RuntimeWarning: More than 20 figures have been opened. Figures created through the pyplot interface (`matplotlib.pyplot.figure`) are retained until explicitly closed and may consume too much memory. (To control this warning, see the rcParam `figure.max_open_warning`).
  max_open_warning, RuntimeWarning)
/anaconda3/lib/python3.7/site-packages/matplotlib/pyplot.py:514: RuntimeWarning: More than 20 figures have been opened. Figures created through the pyplot interface (`matplotlib.pyplot.figure`) are retained until explicitly closed and may consume too much memory. (To control this warning, see the rcParam `figure.max_open_warning`).
  max_open_warning, RuntimeWarning)
/anaconda3/lib/python3.7/site-packages/matplotlib/pyplot.py:514: RuntimeWarning: More than 20 figures have been opened. Figures created through the pyplot interface (`matplotlib.pyplot.figure`) are retained until explicitly closed and may consume too much memo

/anaconda3/lib/python3.7/site-packages/matplotlib/pyplot.py:514: RuntimeWarning: More than 20 figures have been opened. Figures created through the pyplot interface (`matplotlib.pyplot.figure`) are retained until explicitly closed and may consume too much memory. (To control this warning, see the rcParam `figure.max_open_warning`).
  max_open_warning, RuntimeWarning)
/anaconda3/lib/python3.7/site-packages/matplotlib/pyplot.py:514: RuntimeWarning: More than 20 figures have been opened. Figures created through the pyplot interface (`matplotlib.pyplot.figure`) are retained until explicitly closed and may consume too much memory. (To control this warning, see the rcParam `figure.max_open_warning`).
  max_open_warning, RuntimeWarning)
/anaconda3/lib/python3.7/site-packages/matplotlib/pyplot.py:514: RuntimeWarning: More than 20 figures have been opened. Figures created through the pyplot interface (`matplotlib.pyplot.figure`) are retained until explicitly closed and may consume too much memo

/anaconda3/lib/python3.7/site-packages/matplotlib/pyplot.py:514: RuntimeWarning: More than 20 figures have been opened. Figures created through the pyplot interface (`matplotlib.pyplot.figure`) are retained until explicitly closed and may consume too much memory. (To control this warning, see the rcParam `figure.max_open_warning`).
  max_open_warning, RuntimeWarning)
/anaconda3/lib/python3.7/site-packages/matplotlib/pyplot.py:514: RuntimeWarning: More than 20 figures have been opened. Figures created through the pyplot interface (`matplotlib.pyplot.figure`) are retained until explicitly closed and may consume too much memory. (To control this warning, see the rcParam `figure.max_open_warning`).
  max_open_warning, RuntimeWarning)
/anaconda3/lib/python3.7/site-packages/matplotlib/pyplot.py:514: RuntimeWarning: More than 20 figures have been opened. Figures created through the pyplot interface (`matplotlib.pyplot.figure`) are retained until explicitly closed and may consume too much memo

/anaconda3/lib/python3.7/site-packages/matplotlib/pyplot.py:514: RuntimeWarning: More than 20 figures have been opened. Figures created through the pyplot interface (`matplotlib.pyplot.figure`) are retained until explicitly closed and may consume too much memory. (To control this warning, see the rcParam `figure.max_open_warning`).
  max_open_warning, RuntimeWarning)
/anaconda3/lib/python3.7/site-packages/matplotlib/pyplot.py:514: RuntimeWarning: More than 20 figures have been opened. Figures created through the pyplot interface (`matplotlib.pyplot.figure`) are retained until explicitly closed and may consume too much memory. (To control this warning, see the rcParam `figure.max_open_warning`).
  max_open_warning, RuntimeWarning)
/anaconda3/lib/python3.7/site-packages/matplotlib/pyplot.py:514: RuntimeWarning: More than 20 figures have been opened. Figures created through the pyplot interface (`matplotlib.pyplot.figure`) are retained until explicitly closed and may consume too much memo

/anaconda3/lib/python3.7/site-packages/matplotlib/pyplot.py:514: RuntimeWarning: More than 20 figures have been opened. Figures created through the pyplot interface (`matplotlib.pyplot.figure`) are retained until explicitly closed and may consume too much memory. (To control this warning, see the rcParam `figure.max_open_warning`).
  max_open_warning, RuntimeWarning)
/anaconda3/lib/python3.7/site-packages/matplotlib/pyplot.py:514: RuntimeWarning: More than 20 figures have been opened. Figures created through the pyplot interface (`matplotlib.pyplot.figure`) are retained until explicitly closed and may consume too much memory. (To control this warning, see the rcParam `figure.max_open_warning`).
  max_open_warning, RuntimeWarning)
/anaconda3/lib/python3.7/site-packages/matplotlib/pyplot.py:514: RuntimeWarning: More than 20 figures have been opened. Figures created through the pyplot interface (`matplotlib.pyplot.figure`) are retained until explicitly closed and may consume too much memo

/anaconda3/lib/python3.7/site-packages/matplotlib/pyplot.py:514: RuntimeWarning: More than 20 figures have been opened. Figures created through the pyplot interface (`matplotlib.pyplot.figure`) are retained until explicitly closed and may consume too much memory. (To control this warning, see the rcParam `figure.max_open_warning`).
  max_open_warning, RuntimeWarning)
/anaconda3/lib/python3.7/site-packages/matplotlib/pyplot.py:514: RuntimeWarning: More than 20 figures have been opened. Figures created through the pyplot interface (`matplotlib.pyplot.figure`) are retained until explicitly closed and may consume too much memory. (To control this warning, see the rcParam `figure.max_open_warning`).
  max_open_warning, RuntimeWarning)
/anaconda3/lib/python3.7/site-packages/matplotlib/pyplot.py:514: RuntimeWarning: More than 20 figures have been opened. Figures created through the pyplot interface (`matplotlib.pyplot.figure`) are retained until explicitly closed and may consume too much memo

/anaconda3/lib/python3.7/site-packages/matplotlib/pyplot.py:514: RuntimeWarning: More than 20 figures have been opened. Figures created through the pyplot interface (`matplotlib.pyplot.figure`) are retained until explicitly closed and may consume too much memory. (To control this warning, see the rcParam `figure.max_open_warning`).
  max_open_warning, RuntimeWarning)
/anaconda3/lib/python3.7/site-packages/matplotlib/pyplot.py:514: RuntimeWarning: More than 20 figures have been opened. Figures created through the pyplot interface (`matplotlib.pyplot.figure`) are retained until explicitly closed and may consume too much memory. (To control this warning, see the rcParam `figure.max_open_warning`).
  max_open_warning, RuntimeWarning)
/anaconda3/lib/python3.7/site-packages/matplotlib/pyplot.py:514: RuntimeWarning: More than 20 figures have been opened. Figures created through the pyplot interface (`matplotlib.pyplot.figure`) are retained until explicitly closed and may consume too much memo